In [1]:
import h5py 
import numpy as np 
import pandas as pd
import gbm
from astropy.time import Time
from gbm.finder import BurstCatalog
from gbm.finder import TriggerFtp

In [2]:
burstcat = BurstCatalog()
#burstcat.num_rows

Finished in 79 s


In [3]:
burstcat.columns

array(['name', 'ra', 'dec', 'trigger_time', 't90', 't90_error',
       't90_start', 'fluence', 'fluence_error', 'flux_1024',
       'flux_1024_error', 'flux_1024_time', 'flux_64', 'flux_64_error',
       'flnc_band_ampl', 'flnc_band_ampl_pos_err',
       'flnc_band_ampl_neg_err', 'flnc_band_epeak',
       'flnc_band_epeak_pos_err', 'flnc_band_epeak_neg_err',
       'flnc_band_alpha', 'flnc_band_alpha_pos_err',
       'flnc_band_alpha_neg_err', 'flnc_band_beta',
       'flnc_band_beta_pos_err', 'flnc_band_beta_neg_err',
       'flnc_spectrum_start', 'flnc_spectrum_stop',
       'pflx_best_fitting_model', 'pflx_best_model_redchisq',
       'flnc_best_fitting_model', 'flnc_best_model_redchisq',
       'actual_1024ms_interval', 'actual_256ms_interval',
       'actual_64ms_interval', 'back_interval_high_start',
       'back_interval_high_stop', 'back_interval_low_start',
       'back_interval_low_stop', 'bcat_detector_mask', 'bcatalog', 'bii',
       'duration_energy_high', 'duration_energy

In [4]:
c = burstcat.get_table(columns=('trigger_name', 'name','trigger_time',
                                'ra','dec','error_radius','t90','t90_error'))

In [8]:
df = pd.DataFrame(c)

In [9]:
df.loc['GRB191101895']

trigger_name                bn191101895
name                       GRB191101895
trigger_time    2019-11-01 21:28:50.523
ra                               153.71
dec                               18.97
error_radius                       7.84
t90                              10.496
t90_error                         1.086
Name: GRB191101895, dtype: object

In [10]:
gpstime = [Time(t).gps for t in df['trigger_time']]

In [11]:
df['gpstime'] = np.array(gpstime)

In [12]:
df

trigger_name          name             trigger_time          ra  \
GRB120403857  bn120403857  GRB120403857  2012-04-03 20:33:58.493   55.338333   
GRB120227725  bn120227725  GRB120227725  2012-02-27 17:24:41.054  256.730000   
GRB141205018  bn141205018  GRB141205018  2014-12-05 00:25:29.813  294.610000   
GRB180630467  bn180630467  GRB180630467  2018-06-30 11:11:54.405   48.958750   
GRB170116238  bn170116238  GRB170116238  2017-01-16 05:43:15.259   72.940000   
...                   ...           ...                      ...         ...   
GRB210624041  bn210624041  GRB210624041  2021-06-24 00:58:23.248  119.320000   
GRB091012783  bn091012783  GRB091012783  2009-10-12 18:47:02.770  109.400000   
GRB130528695  bn130528695  GRB130528695  2013-05-28 16:41:24.409  138.737917   
GRB090813174  bn090813174  GRB090813174  2009-08-13 04:10:42.593  225.802083   
GRB110201399  bn110201399  GRB110201399  2011-02-01 09:35:10.251  137.580000   

                    dec  error_radius     t90  t90_error       gpstime  
GRB120403857 -89.009167        0.0011   4.288      1.935  1.017520e+09  
GRB120227725 -88.860000        1.2100  17.408      0.810  1.014399e+09  
GRB141205018 -87.580000        3.9000  13.056      1.280  1.101774e+09  
GRB180630467 -87.478611        0.0010  12.032      1.864  1.214392e+09  
GRB170116238 -87.430000        9.3700   9.216      3.620  1.168581e+09  
...                 ...           ...     ...        ...           ...  
GRB210624041  87.110000        4.6400   0.304      0.333  1.308532e+09  
GRB091012783  87.270000        2.4500   0.704      2.499  9.394084e+08  
GRB130528695  87.270000        0.0500  55.553      1.864  1.053795e+09  
GRB090813174  88.568611        0.0017   7.552      0.362  9.341719e+08  
GRB110201399  88.605278        0.0001   8.192      0.870  9.805881e+08  

[3292 rows x 9 columns]

In [13]:
df.to_csv('fermi_burstcat.csv',index=False)

In [11]:
df_fermi = df

# Selection by observation run

In [2]:
tO1_start = Time('2015-09-12T00:00:00')
tO1_end = Time('2016-01-19T16:00:00')

tO2_start = Time('2016-11-30T16:00:00')
tO2_end = Time('2017-08-25T22:00:00')

tO3a_start = Time('2019-04-01T15:00:00')
tO3a_end = Time('2019-10-01T15:00:00')

tO3b_start = Time('2019-11-01T15:00:00')
tO3b_end = Time('2020-03-27T17:00:00')

In [221]:
lgrbsort = {}

with h5py.File('./fermi_lgrb_candidate.hdf','w') as f:
    for obrun in ['o1','o2','o3a','o3b']:
        if obrun == 'o3b':
            ltime = (df['trigger_time'] < tO3b_end) & (df['trigger_time']> tO3b_start)
        elif obrun == 'o3a':
            ltime = (df['trigger_time'] < tO3a_end) & (df['trigger_time']> tO3a_start)
        elif obrun == 'o2':
            ltime = (df['trigger_time'] < tO2_end) & (df['trigger_time']> tO2_start)
        elif obrun == 'o1':
            ltime = (df['trigger_time'] < tO1_end) & (df['trigger_time']> tO1_start)
        
        lt90 = (df['t90']-abs(df['t90_error']))>4
        
        lgrb =df[ltime & lt90]
        lgrbsort[obrun] = lgrb.sort_values(by='trigger_time')
        
        f['{}/name'.format(obrun)] = lgrbsort[obrun]['name'].values
        f['{}/trigger_name'.format(obrun)] = lgrbsort[obrun]['trigger_name'].values
        f['{}/gps'.format(obrun)] = lgrbsort[obrun]['gpstime'].values
        f['{}/ra'.format(obrun)] = lgrbsort[obrun]['ra'].values
        f['{}/dec'.format(obrun)] = lgrbsort[obrun]['dec'].values
        f['{}/error_radius'.format(obrun)] = lgrbsort[obrun]['error_radius'].values

# Swift

In [14]:
df = pd.read_table('./summary_general.txt', delimiter='|', header=22)

# Some data cleaning

In [15]:
df.replace('\s+','',regex=True,inplace=True)

In [16]:
df.columns = [c.replace(' ','') for c in df.columns]
df.columns = [c.replace('#','') for c in df.columns]

In [17]:
#for col in df.columns:
#    df = df[df[col]!='N/A']

In [18]:
for col in ['Trig_time_UTC','T90','T90_err']:
    df = df[df[col]!='N/A']

In [19]:
df

GRBname Trig_ID  Trig_time_met               Trig_time_UTC  \
0     GRB200829A  993768  620402400.000  2020-08-29T13:59:34.457300   
1     GRB200819A  992099  619544658.368  2020-08-19T15:43:52.881500   
2     GRB200809B  987745  618680512.420       20200809T15:41:26.928   
3     GRB200806A  987016  618420555.328  2020-08-06T15:28:49.915180   
4     GRB200729A  984929  617744310.464  2020-07-29T19:38:05.095420   
...          ...     ...            ...                         ...   
1385   GRB041223  100585  125503577.280  2004-12-23T14:06:17.956380   
1386   GRB041220  100433  125276305.920  2004-12-20T22:58:26.599560   
1387  GRB041219C  100380  125181033.000  2004-12-19T20:30:34.000000   
1388  GRB041219B  100368  125163527.319         2004-12-19T15:38:48   
1390   GRB041217  100116  124961305.236  2004-12-17T07:28:25.236000   

         RA_ground     DEC_ground Image_position_err     Image_SNR  \
0     2.511393e+02   7.236396e+01       1.821205e+00  1.291746e+01   
1     2.151284e+01   6.306401e+01       2.066521e+00  1.078390e+01   
2     1.588788e+01  -7.383024e+01       2.030407e+00  1.106040e+01   
3     5.293437e+01   3.707842e+01       7.538071e-01  4.554712e+01   
4     1.843603e+02   4.557053e+01       2.318689e+00  9.148365e+00   
...            ...            ...                ...           ...   
1385  1.001856e+02  -3.707220e+01       4.934437e-01  8.343541e+01   
1386  2.913007e+02   6.059630e+01       9.662489e-01  3.194624e+01   
1387  3.438824e+02  -7.678556e+01       1.796621e+00  1.317070e+01   
1388  1.676888e+02  -3.346167e+01       2.026961e+00  1.108727e+01   
1390  1.647929e+02  -1.794047e+01       1.374749e+00  1.930439e+01   

               T90       T90_err           T50       T50_err  \
0     1.310000e+01  3.079558e+00  2.684000e+00  4.882629e-02   
1     2.694400e+01  7.060334e+00  1.145600e+01  6.706272e+00   
2     4.200000e+00  6.278089e-01  2.448000e+00  7.850733e-01   
3     3.868800e+01  1.004064e+00  1.455600e+01  3.314453e-01   
4     1.220000e+02  3.423449e+01  5.700000e+01  2.482438e+01   
...            ...           ...           ...           ...   
1385  1.090600e+02  1.803933e+00  2.919600e+01  6.114769e-01   
1386  5.584000e+00  1.113352e+00  2.200000e+00  3.261656e-01   
1387  1.000000e+01  1.000000e+00  4.000000e+00  1.000000e+00   
1388  9.856000e+00  1.869194e+01  5.952000e+00  1.132276e+00   
1390  5.668000e+00  7.297123e-01  2.700000e+00  2.512051e-01   

     Evt_start_sincetrig Evt_stop_sincetrig   pcode  Trigger_method  \
0                   -239                963  0.8828    imagetrigger   
1                   -239                963  0.9609     ratetrigger   
2                    -49                151  0.2402  grounddetected   
3                   -239                963  0.5703     ratetrigger   
4                   -239                963  0.4609     ratetrigger   
...                  ...                ...     ...             ...   
1385                -299                303  0.4766     ratetrigger   
1386                -300                302  0.8672     ratetrigger   
1387                  -3                 17  0.4453     ratetrigger   
1388                  15                 54  0.7734     ratetrigger   
1390                  -2                 18  0.2969     ratetrigger   

     XRT_detection comment  
0              Yes          
1              Yes          
2              Yes          
3              Yes          
4              Yes          
...            ...     ...  
1385            No          
1386            No          
1387            No          
1388            No          
1390            No          

[1360 rows x 18 columns]

In [20]:
def cleantime(t):
    cleant = t
    if t[4]!='-':
        cleant = t[:4]+'-'+t[4:6]+'-'+t[6:]
    return cleant

In [21]:
gpstime = [Time(cleantime(t.replace(' ',''))).gps for t in df['Trig_time_UTC'].values]

In [22]:
df['gpstime'] = np.array(gpstime)

In [23]:
df[df['GRBname']=='GRB191130A']

GRBname      Trig_ID  Trig_time_met            Trig_time_UTC  \
47  GRB191130A  03110538005  596811926.376  2019-11-30T13:05:02.316   

       RA_ground    DEC_ground Image_position_err     Image_SNR           T90  \
47  1.330794e+02  4.995746e+00       1.162246e+00  2.454099e+01  1.756000e+01   

         T90_err           T50       T50_err Evt_start_sincetrig  \
47  2.876871e+00  6.004000e+00  1.280695e+00                -139   

   Evt_stop_sincetrig pcode  Trigger_method XRT_detection comment  \
47                106   N/A  grounddetected            No           

         gpstime  
47  1.259154e+09

In [24]:
df.to_csv('swift_catalog.csv',index=False)

In [84]:
tO1_start = Time('2015-09-12T00:00:00')
tO1_end = Time('2016-01-19T16:00:00')

tO2_start = Time('2016-11-30T16:00:00')
tO2_end = Time('2017-08-25T22:00:00')

tO3a_start = Time('2019-04-01T15:00:00')
tO3a_end = Time('2019-10-01T15:00:00')

tO3b_start = Time('2019-11-01T15:00:00')
tO3b_end = Time('2020-03-27T17:00:00')

In [85]:
swiftsort = {}
try:
    file.close()
except NameError:
    pass
file = h5py.File('./swift_lgrb_candidate.hdf', 'w')
for obrun in ['o1','o2','o3a','o3b']:
    if obrun == 'o3b':
        ltime = (df['gpstime'] < tO3b_end.gps) & (df['gpstime']> tO3b_start.gps)
    elif obrun == 'o3a':
        ltime = (df['gpstime'] < tO3a_end.gps) & (df['gpstime']> tO3a_start.gps)
    elif obrun == 'o2':
        ltime = (df['gpstime'] < tO2_end.gps) & (df['gpstime']> tO2_start.gps)
    elif obrun == 'o1':
        ltime = (df['gpstime'] < tO1_end.gps) & (df['gpstime']> tO1_start.gps)
    
    lt90 = df['T90'].astype(float)-abs(df['T90_err'].astype(float))>4
    lgrb =df[ltime & lt90]
    swiftsort[obrun] = lgrb.sort_values(by='gpstime')
    file['{}/name'.format(obrun)] = swiftsort[obrun]['GRBname'].values
    file['{}/gpstime'.format(obrun)] = swiftsort[obrun]['gpstime'].astype(float)
    file['{}/ra'.format(obrun)] = swiftsort[obrun]['RA_ground'].astype(float)
    file['{}/dec'.format(obrun)] = swiftsort[obrun]['DEC_ground'].astype(float)
    #file['{}/position_err'.format(obrun)] = swiftsort[obrun]['Image_position_err'].values
file.close()

In [89]:
np.max(df_fermi['t90'])

984.084